In [ ]:
require 'faraday'
require 'moneta'
require 'parallel'

backend_url = 'http://cashbee-admin-mengmai.comein.club'
auth_token = 'b974f6c0-75cb-4239-bbc7-a11ca7f3fa92'

"b974f6c0-75cb-4239-bbc7-a11ca7f3fa92"

In [ ]:
### data import

conn = Faraday.new(
  url: backend_url,
  headers: {'X-Auth-Token' => auth_token})

cur_page = 1
json = JSON.parse(conn.get("/yolo-loan/admin/loanInfo/selectLoanContractListByFirstPartyId?page=#{cur_page}&limit=50").body)
pageCount = json["pageCount"].to_i
dataCount = json["dataCount"].to_i

puts "pageCount - #{pageCount}"
puts "dataCount - #{dataCount}"


pageCount - 150
dataCount - 7474


In [ ]:
pages = (1..pageCount)
loan_data = Parallel.map(pages, in_threads: 5) do |cur_page|
    puts cur_page if cur_page % 10 == 0

    response = conn.get("/yolo-loan/admin/loanInfo/selectLoanContractListByFirstPartyId?page=#{cur_page}&limit=50") 
    json = JSON.parse(response.body)
    json["data"]
end

loan_data = loan_data.flatten

nil

10
20
30
40
50
60
70
80
90
100
110
120
130
140
150


[[{"platformLoanUserId"=>"1474319227632062465", "mobile"=>"+919971369992", "loanReviewNo"=>"I150417406833564057646", "productName"=>"productZ10", "loanAmount"=>2000.0, "withdrawAmount"=>1661.0, "repayAmount"=>0.0, "loanDays"=>15, "rate"=>"36.00%", "loanNo"=>"IL150417406831047475288", "loanStartTime"=>"2022-03-17", "loanEndTime"=>"2022-03-31", "loanState"=>"还款中", "finishTime"=>nil, "firstPartyName"=>"alfred", "lineOfCredit"=>"2000", "nbfcKey"=>"zavron", "interestAmount"=>29.59, "fineAmount"=>0.0, "serviceAmount"=>339.0, "serviceTaxAmount"=>61.0, "unpaidInterestAmount"=>29.59, "unpaidFineAmount"=>0.0, "unpaidServiceAmount"=>339.0, "unpaidServiceTaxAmount"=>61.0, "principal"=>1600.0}, {"platformLoanUserId"=>"1453983276948582402", "mobile"=>"+918208464014", "loanReviewNo"=>"I150411462664676966402", "productName"=>"productZ10", "loanAmount"=>15000.0, "withdrawAmount"=>12458.0, "repayAmount"=>0.0, "loanDays"=>15, "rate"=>"36.00%", "loanNo"=>"IL150411462661740953651", "loanStartTime"=>"2022-0

In [ ]:
users = loan_data.map {|x| x["platformLoanUserId"]}.uniq.sort
puts "users_count - #{users.count}"

user_data = Parallel.map(users, in_threads: 10) do |cur_user|
    response = conn.get("yolo-loan/admin/loanUserManage/getLoanRecordList?page=1&limit=20&platformLoanUserId=#{cur_user}") 
    json = JSON.parse(response.body)
    json["data"].map {|x| x["platformLoanUserId"]=cur_user; x}
end

user_data = user_data.flatten

nil



users_count - 7143


In [ ]:

# Create a simple file store
store = Moneta.new(:File, dir: '/home/jovyan/work/loan_data')

# Store some entries
store['loan_data'] = loan_data
store['user_data'] = user_data

# # Read entry
# store.key?('loan_data') # returns true
# read_data = store['loan_data'] # returns 'value'

store.close

<a style='text-decoration:none;line-height:16px;display:flex;color:#5B5B62;padding:10px;justify-content:end;' href='https://deepnote.com?utm_source=created-in-deepnote-cell&projectId=ebde59c2-d67b-4e31-ad3b-1bdd07014691' target="_blank">
 </img>
Created in <span style='font-weight:600;margin-left:4px;'>Deepnote</span></a>